In [ ]:
import cv2
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
import frameAnalysis as fa
from matplotlib.animation import FuncAnimation
from matplotlib.offsetbox import OffsetImage, AnnotationBbox

# Image Processing, Machine Learning, and Object Detection

Loading saved ML model for object detection:

In [ ]:
model_url = "model/archive/"
model = tf.saved_model.load(model_url)

I have created a Python module, **frameAnalysis** that contains functions that handle general tasks such as preprocessing, object detection, etc.


`load_and_preprocess_image`:

Loads image from filepath if not already loaded, converts to RGB tensor and properly shapes for object detection



`visualize_results`

uses detections returned from ML model to create bounding boxes for the pets detected in an image above a specified confidence level

`resize_image`

resizes shape of image array while maintaining original aspect ratio

`get_pet_boxes`

similar to visualize_results, but also implements Non Maximum Suppression to consolidate all detected boxes into bounding boxes for the pets detected in an image

`track_pets`

implements specified tracking algorithm to track initial boxes detected after NMS, returns array of pet coordinates and boxes for animation, can create MP4 recording of tracking



<dl>

# Testing Pet Detection with Google Mobilenet V2 ML model

Below are some tests I ran to figure out how to properly detect pets in an image.
My current implementation is limited to one class of pet (cat or dog) per image/video.

In [ ]:
image = cv2.imread("images/kilala_jojo_detect_test_01.jpeg")
processes_image = fa.load_and_preprocess_image(image)
try:
    detections = model(processes_image)
except Exception as e:
    print("Error during model inference:", e)

In [ ]:
image = cv2.imread("images/kilala_jojo_detect_test_01.jpeg")
image = fa.resize_image(image, image.shape[0] // 8, image.shape[1] // 8)
fa.visualize_results(image, detections)

In [ ]:
image = "images/kilala_detect_test_02.jpeg"
processes_image = fa.load_and_preprocess_image(image)

detections_2 = model(processes_image)
fa.visualize_results(cv2.imread(image), detections_2)

In [ ]:
image_path = "images/cody_funny.jpeg"
image = cv2.imread(image_path)

image = fa.resize_image(image, image.shape[0] // 3, image.shape[1] // 3)

processes_image = fa.load_and_preprocess_image(image)

detections_2 = model(processes_image)
fa.visualize_results(image, detections_2, pet_class_id=18)

In [ ]:
image_path = "images/koga.jpeg"
image = cv2.imread(image_path)

image = fa.resize_image(image, image.shape[0] // 8, image.shape[1] // 8)
processes_image = fa.load_and_preprocess_image(image)

detections_2 = model(processes_image)
fa.visualize_results(image, detections_2)

In [ ]:
image_path = "images/kilala_jojo_couch.jpeg"
image = cv2.imread(image_path)

image = fa.resize_image(image, image.shape[0] // 3, image.shape[1] // 3)
processes_image = fa.load_and_preprocess_image(image)

detections_2 = model(processes_image)
fa.visualize_results(image, detections_2)

# Pet Movement Tracking

Here, we load mp4 videos and use our `track_pets` method to detect our inital pet positions, create trackers for each pet detection box, and update the box as the pet moves through the video.

We are using the CSRT (Discriminative Correlation Filter with Channel and Spatial Reliability) tracking algorithm to track and record the movement of each pet, since CSRT can handle occlusion and scale variations really well.

In [ ]:
video_path = "images/kilala_baby_jojo.mp4"
output_video_path = "output_kilala_baby_jojo.mp4"

pet_positions_1 = fa.track_pets(model, video_path, output_video_path, confidence=0.5)

In [ ]:
video_path = "images/jojo_koga_fight.mp4"
output_video_path = "output_kilala_koga.mp4"
pet_positions = fa.track_pets(
    model,
    video_path,
    output_video_path,
    confidence=0.3,
    pet_class_id=17,
)

# Creating Animations

Since our `track_pets` method returns `pet_positions`, the coordinates for all pets in the video for every frame, can use this data to plot and animate the movement of each individual cat.

Here we mostly use matplot's built in functions to create gif animations

In [ ]:
fig, ax = plt.subplots()
plt.axis("equal")


# Function to update the plot in each animation frame
def update(frame):
    ax.clear()
    plt.axis("equal")
    ax.set_xlim(0, 960)
    ax.set_ylim(0, 540)
    for pet_id, coord in enumerate(pet_positions[frame]):
        x, y = coord
        ax.plot(x, 540 - y, marker="o", markersize=8, label=f"Pet {pet_id + 1}")

    ax.set_title(f"Frame {frame + 1}")
    ax.legend()


animation = FuncAnimation(fig, update, frames=len(pet_positions), blit=False)

animation.save("jojo_baby_koga.gif", fps=10)

In [ ]:
fig, ax = plt.subplots()
plt.axis("equal")


def update(frame):
    ax.clear()
    ax.imshow(bg_img, extent=[0, 960, 0, 540], aspect="auto")
    plt.axis("equal")
    ax.set_xlim(0, 1920 // 2)
    ax.set_ylim(0, 1080 // 2)
    for pet_id, coord in enumerate(pet_positions_1[frame]):
        x, y = coord
        ax.plot(
            x + 150, 540 - y + 100, marker="o", markersize=8, label=f"Pet {pet_id + 1}"
        )

    ax.set_title(f"Frame {frame + 1}")
    ax.legend()


animation = FuncAnimation(fig, update, frames=len(pet_positions_1), blit=False)

animation.save("kilala_baby_jojo.gif", fps=60)

The fun part, using **custom, resizable markers** for our plot animations! These are original icons created by my partner, *Angelique Echeveste*, a student here at Cal majoring in Art History.

The idea here is that we can now create animations that simulate the movement of pets through an open space. Resizing the markers allows us to emulate movement between the foreground and background of the video.

The rest of this notebook will contain scripts that create different animations using pet position data, custom markers, and image processing techniques. 

In [ ]:

fig, ax = plt.subplots()
plt.axis("equal")

pet_mapping = {0: "Jojo", 1: "Koga"}
pet_markers = [plt.imread(fa.PET_PNGS[pet]) for pet in pet_mapping.values()]


# Function to update the plot in each animation frame
def update(frame):
    ax.clear()
    plt.axis("equal")
    ax.set_xlim(0, 960)
    ax.set_ylim(0, 540)
    for pet_id, coord in enumerate(pet_positions[frame]):
        x, y = coord

        marker_img = pet_markers[pet_id]
        imagebox = OffsetImage(marker_img, zoom=0.095)
        ab = AnnotationBbox(imagebox, (x, 540 - y), frameon=False)
        ax.add_artist(ab)

    ax.set_title(f"Frame {frame + 1}")


animation = FuncAnimation(fig, update, frames=len(pet_positions), blit=False)

animation.save("jojo_baby_koga_markers.gif", fps=10, dpi=300)

In [ ]:
# WITH MARKERS
fig, ax = plt.subplots()
plt.axis("equal")

pet_mapping = {0: "Jojo", 1: "Kilala"}
pet_markers = [plt.imread(fa.PET_PNGS[pet]) for pet in pet_mapping.values()]


# Function to update the plot in each animation frame
def update(frame):
    ax.clear()
    plt.axis("equal")
    ax.set_xlim(0, 960)  # Adjust these values based on your video resolution
    ax.set_ylim(0, 540)
    for pet_id, coord in enumerate(pet_positions_1[frame]):
        x, y = coord

        marker_img = pet_markers[pet_id]
        imagebox = OffsetImage(marker_img, zoom=0.065)  # Adjust the zoom factor
        ab = AnnotationBbox(imagebox, (x + 150, 540 - y + 100), frameon=False)
        ax.add_artist(ab)

    ax.set_title(f"Frame {frame + 1}")


# Create the animation
animation = FuncAnimation(fig, update, frames=len(pet_positions_1), blit=False)

# Save the animation as a GIF
animation.save(
    "outputs/kilala_baby_jojo_markers.gif", writer="imagemagick", fps=10, dpi=300
)

In [ ]:
video_path = "images/cody_runs.mp4"
output_video_path = "outputs/output_cody_runs.mp4"


cody_positions = fa.track_pets(
    model, video_path, output_video_path, confidence=0.2, pet_class_id=18, record=True
)

In [ ]:
background_img_path = "assets/cody_background.jpg"
bg_img = plt.imread(background_img_path)
bg_img = np.rot90(np.rot90(bg_img))

fig, ax = plt.subplots()
plt.axis("equal")

pet_mapping = {0: "Cody"}
pet_markers = [plt.imread(fa.PET_PNGS[pet]) for pet in pet_mapping.values()]


# Function to update the plot in each animation frame
def update(frame):
    ax.clear()

    plt.axis("equal")
    ax.set_xlim(0, 960)
    ax.set_ylim(0, 540)
    for pet_id, coord in enumerate(cody_positions[frame]):
        x, y = coord

        marker_img = pet_markers[pet_id]
        imagebox = OffsetImage(marker_img, zoom=0.095)
        ab = AnnotationBbox(imagebox, (960 - x - 150, 540 - y), frameon=False)
        ax.add_artist(ab)
    ax.imshow(bg_img, extent=[960, 0, 540, 0], aspect="auto")
    ax.set_title(f"Frame {frame + 1}")


animation = FuncAnimation(fig, update, frames=len(cody_positions), blit=False)

animation.save("outputs/cody_runs_markers_1.gif", fps=20, dpi=100)

In [ ]:
video_path = "images/cody_runs.mp4"

cap = cv2.VideoCapture(video_path)
ret, frame = cap.read()
frame = fa.resize_image(frame, frame.shape[1] // 2, frame.shape[0] // 2)

cv2.imwrite("assets/cody_background.jpg", frame)